# Prepare OpenQuake Liquefaction Scenarios

In [29]:
# Import dependencies
import os, glob
import pandas as pd
import copy
from openquake.engine.engine import create_jobs

# Ruptures information
rup_info = pd.read_csv('rupture_trts.csv')

In [30]:
rup_info

#                          Event Name    Mw TRT (in repo)  \
0    1                        1664_N_Bang  7.70          ascr   
1    2                        1762_arakan  8.50          subd   
2    3                               1822  7.10          subd   
3    4                        1869_cachar  7.30          ascr   
4    5                     1885_manikganj  7.20          ascr   
5    6                         1897_Dauki  8.70          subd   
6    7                     1918_Srimangal  7.40          ascr   
7    8                   chittagong_north  8.20          subd   
8    9          chittagong_thrust_smaller  7.25          ascr   
9   10                         sikkim_mht  8.50          subd   
10  11  western_deformation_front_partial  7.70          ascr   
11  12          western_deformation_front  8.50          ascr   

           TRT (JSON ref)  Rake                 gmmLT            gmmLT-Lana  
0    active shallow crust    90            gmmLT_ascr  gmpe_logic_tree_ascr  
1    subdcution interface    90  subduction interface  gmpe_logic_tree_subd  
2    active shallow crust    90            gmmLT_ascr  gmpe_logic_tree_ascr  
3    active shallow crust    90            gmmLT_ascr  gmpe_logic_tree_ascr  
4    active shallow crust    90  subduction interface  gmpe_logic_tree_ascr  
5    active shallow crust    90            gmmLT_ascr  gmpe_logic_tree_subd  
6    subduction interface    90  subduction interface  gmpe_logic_tree_subd  
7    subduction interface    90  subduction interface  gmpe_logic_tree_subd  
8    subduction interface    90            gmmLT_ascr  gmpe_logic_tree_ascr  
9    subduction interface    90  subduction interface  gmpe_logic_tree_subd  
10   active shallow crust    90            gmmLT_ascr  gmpe_logic_tree_ascr  
11   active shallow crust    90            gmmLT_ascr  gmpe_logic_tree_ascr

In [31]:
# Configuration file template
job_template = '''
[General]
description = Bangladesh scenario {NAME} - liquefaction
calculation_mode = scenario
random_seed = 113

[site_params]
site_model_file = ../Site_model.csv
region_grid_spacing = 5

[rupture]
rupture_model_file = {RUPTURE_FILE}
rupture_mesh_spacing = 2.0

[Secondary perils]
sensitivity_analysis = {'secondary_perils': ['AllstadtEtAl2022Liquefaction', 'TodorovicSilva2022NonParametric']}

[Calculation parameters]
intensity_measure_types = PGV, PGA
cross_correlation = Bradley2012
truncation_level = 3
maximum_distance = 300
number_of_ground_motion_fields = 1000
gsim_logic_tree_file = ../gmmLT_ref/{gmpe_file}
extreme_gmv = {"PGV": 150, "PGA": 2.5}
'''

In [32]:
# Create job files for each rupture
for i, event in enumerate(rup_info['Event Name']):
    job = copy.deepcopy(job_template)  
    # Remove spaces from the event name to create the rupture name
    rupture = f'bangladesh_{event.replace(" ", "_")}_scenario_rupture.xml'

    # Fetch the required information from the CSV file
    gsimLT = rup_info.loc[rup_info['Event Name'] == event, 'gmmLT-Lana'].values[0]
    gsimLT += ".xml"
    
    job = job.replace(
        '{NAME}', event).replace(
        '{RUPTURE_FILE}', rupture).replace(
        '{gmpe_file}', gsimLT)
    
    with open(f'job_{event}.ini', 'w', encoding="utf-8") as f:
        f.write(job)
    
    print('job file saved for:', event)


job file saved for: 1664_N_Bang
job file saved for: 1762_arakan
job file saved for: 1822
job file saved for: 1869_cachar
job file saved for: 1885_manikganj
job file saved for: 1897_Dauki
job file saved for: 1918_Srimangal
job file saved for: chittagong_north
job file saved for: chittagong_thrust_smaller
job file saved for: sikkim_mht
job file saved for: western_deformation_front_partial
job file saved for: western_deformation_front
